### K-Prototype
* This notebook show the process of K-prototype clustering algorithm. 
* 514 features were selected out of the 1063 features. See the details in separate feature selection files.
* A subsample data set is used (1.25% of the original size data)

In [21]:
from sklearn.cluster import KMeans
import pandas as pd
import numpy as np
from scipy.spatial.distance import cdist, pdist
from sklearn.preprocessing import StandardScaler
from matplotlib import pyplot as plt
from sklearn.metrics import silhouette_score, silhouette_samples
from kmodes.kprototypes import KPrototypes
%matplotlib inline

#### K-prototype on a subsample data (1.25% of the original size data)

In [6]:
def process_data(file, categorical):
    '''
    Process the original data
    * Feature selection 514/1064
    * Impute missing values with means
    * return the new values, the index of categorical data, 
    and the policy number column
    '''
    df = pd.read_csv(file, low_memory=False)
    df.drop('Unnamed: 0', axis=1, inplace=True)
    selected_variable = pd.read_csv('selectedVariables.csv')
    selected_variable.drop('Unnamed: 0', axis=1, inplace=True)
    df1 = df[df.columns.intersection(selected_variable.columns)]
    PolNum = np.asarray(df1.PolNum_UW)
    df2 = df1.iloc[:, :-1]
    
    # Separate numerical and categorical data
    # Select integers and turn to float
    df_num_int = df2.select_dtypes(include=['int64'])
    df_num_int = df_num_int.astype(float)
    # Select float
    df_num_float = df2.select_dtypes(include=['float64'])
    # Select categorical values
    df_cat = df2.select_dtypes(include=['object'])
    # Impute missing values with means

    df_num_int = df_num_int.fillna(df_num_int.mean())

    df_num_float = df_num_float.fillna(df_num_float.mean())
    print(df_num_int.shape, df_num_float.shape, df_cat.shape)
    X = pd.concat([df_num_int, df_num_float, df_cat], axis=1)
    X1 = StandardScaler().fit_transform(X)
    X1 = X1.values
    categorical = categorical
    return X1, categorical, PolNum

def encode_features(X, enc_map=None):
    """Converts categorical values in each column of X to integers in the range
    [0, n_unique_values_in_column - 1], if X is not already of integer type.
    If mapping is not provided, it is calculated based on the values in X.
    Unknown values during prediction get a value of -1. np.NaNs are ignored
    during encoding, and get treated as unknowns during prediction.
    """
    if np.issubdtype(X.dtype, np.integer):
        # Already integer type, so we can take a shortcut. Simply reshape
        # the data to mapping dictionaries, and do nothing with X.
        enc_map = [{val: val for val in np.unique(col)} for col in X.T]
        return X, enc_map

    if enc_map is None:
        fit = True
        # We will calculate enc_map, so initialize the list of column mappings.
        enc_map = []
    else:
        fit = False

    Xenc = np.zeros(X.shape).astype('int')
    for ii in range(X.shape[1]):
        
        if fit:
            col_enc = {val: jj for jj, val in enumerate(np.unique(X[:, ii][~pd.isnull(X[:, ii])]))
                       if not (isinstance(val, float) and np.isnan(val))}
            enc_map.append(col_enc)
        # Unknown categories (including np.NaNs) all get a value of -1.
        Xenc[:, ii] = np.array([enc_map[ii].get(x, -1) for x in X[:, ii]])

    return Xenc, enc_map


In [3]:
X, categorical, PolNum = process_data('PHBsample14_sss.csv', range(498, 513))

In [4]:
# Process categorical variables
Xenc, enc_map = encode_features(X, enc_map=None)

In [19]:
# Standarize the data points
Xenc_sc = StandardScaler().fit_transform(Xenc)

/home/capsops/.conda/envs/capsenvs/lib/python3.6/site-packages/sklearn/utils/validation.py:475: DataConversionWarning: Data with input dtype int64 was converted to float64 by StandardScaler.
  warnings.warn(msg, DataConversionWarning)


In [36]:
kproto = KPrototypes(n_clusters=8, init='Cao', verbose=2)
clusters = kproto.fit_predict(Xenc_sc, categorical=range(498, 513))
print('Total cost of the algorithm: ', kproto.cost_)
print('Total number of iterations: ', kproto.n_iter_)
score = silhouette_score(Xenc_sc, kproto.labels_, sample_size=30000)
print('Silhouette score Kprototype: ', score)

Initialization method and algorithm are deterministic. Setting n_init to 1.
Init: initializing centroids
Init: initializing clusters
Starting iterations...
Run: 1, iteration: 1/100, moves: 42656, ncost: 26135431.23490165
Run: 1, iteration: 2/100, moves: 12063, ncost: 25975298.309271395
Run: 1, iteration: 3/100, moves: 7597, ncost: 25846883.920766808
Run: 1, iteration: 4/100, moves: 6251, ncost: 25773888.927163955
Run: 1, iteration: 5/100, moves: 4663, ncost: 25737736.59101129
Run: 1, iteration: 6/100, moves: 3457, ncost: 25717987.713154767
Run: 1, iteration: 7/100, moves: 2344, ncost: 25707732.263157133
Run: 1, iteration: 8/100, moves: 1768, ncost: 25701138.220084403
Run: 1, iteration: 9/100, moves: 1384, ncost: 25696338.287111755
Run: 1, iteration: 10/100, moves: 1083, ncost: 25693230.690356746
Run: 1, iteration: 11/100, moves: 902, ncost: 25691166.40405122
Run: 1, iteration: 12/100, moves: 728, ncost: 25689764.232772063
Run: 1, iteration: 13/100, moves: 605, ncost: 25688896.204097502

In [37]:
result = {}
for s, c in zip(PolNum, clusters):
    print("PolNum: {}, clusters:{}".format(s, c))
    result[s] = c
import csv
with open('K-proto_result_8clusters.csv', 'w') as f:  
    w = csv.DictWriter(f, result.keys())
    w.writeheader()
    w.writerow(result)

PolNum: 294692, clusters:4
PolNum: 281394, clusters:2
PolNum: 475776, clusters:6
PolNum: 288738, clusters:4
PolNum: 15320, clusters:0
PolNum: 377167, clusters:5
PolNum: 169497, clusters:5
PolNum: 12245, clusters:7
PolNum: 414626, clusters:7
PolNum: 147008, clusters:5
PolNum: 70840, clusters:0
PolNum: 141388, clusters:5
PolNum: 42495, clusters:5
PolNum: 26674, clusters:4
PolNum: 231534, clusters:5
PolNum: 90883, clusters:5
PolNum: 91678, clusters:5
PolNum: 106979, clusters:5
PolNum: 472951, clusters:7
PolNum: 415082, clusters:6
PolNum: 461943, clusters:2
PolNum: 56106, clusters:1
PolNum: 293174, clusters:4
PolNum: 315646, clusters:6
PolNum: 49751, clusters:7
PolNum: 258001, clusters:1
PolNum: 111566, clusters:6
PolNum: 497199, clusters:6
PolNum: 251999, clusters:3
PolNum: 80496, clusters:7
PolNum: 369228, clusters:5
PolNum: 289246, clusters:2
PolNum: 217750, clusters:7
PolNum: 44872, clusters:7
PolNum: 462073, clusters:1
PolNum: 111004, clusters:2
PolNum: 458273, clusters:6
PolNum: 2107

PolNum: 369289, clusters:7
PolNum: 446563, clusters:7
PolNum: 381200, clusters:0
PolNum: 37140, clusters:1
PolNum: 204196, clusters:1
PolNum: 114545, clusters:7
PolNum: 199731, clusters:5
PolNum: 172327, clusters:1
PolNum: 115923, clusters:6
PolNum: 376546, clusters:2
PolNum: 358789, clusters:7
PolNum: 253369, clusters:5
PolNum: 221133, clusters:6
PolNum: 403490, clusters:3
PolNum: 148512, clusters:4
PolNum: 467452, clusters:2
PolNum: 48321, clusters:5
PolNum: 297365, clusters:1
PolNum: 224407, clusters:5
PolNum: 310698, clusters:5
PolNum: 499966, clusters:1
PolNum: 345084, clusters:0
PolNum: 199471, clusters:6
PolNum: 325373, clusters:2
PolNum: 103591, clusters:5
PolNum: 508616, clusters:2
PolNum: 132053, clusters:7
PolNum: 104040, clusters:4
PolNum: 221169, clusters:7
PolNum: 510963, clusters:7
PolNum: 228761, clusters:2
PolNum: 400061, clusters:6
PolNum: 9500, clusters:6
PolNum: 124566, clusters:5
PolNum: 6720, clusters:5
PolNum: 461756, clusters:4
PolNum: 329593, clusters:2
PolNum:

PolNum: 267690, clusters:6
PolNum: 511428, clusters:5
PolNum: 155956, clusters:2
PolNum: 98561, clusters:4
PolNum: 2500, clusters:0
PolNum: 22917, clusters:5
PolNum: 56387, clusters:6
PolNum: 153804, clusters:5
PolNum: 180872, clusters:0
PolNum: 28413, clusters:5
PolNum: 77092, clusters:6
PolNum: 303775, clusters:0
PolNum: 355717, clusters:6
PolNum: 105563, clusters:2
PolNum: 183295, clusters:7
PolNum: 493906, clusters:6
PolNum: 491230, clusters:5
PolNum: 346520, clusters:2
PolNum: 490730, clusters:7
PolNum: 485996, clusters:4
PolNum: 121633, clusters:4
PolNum: 201653, clusters:6
PolNum: 181345, clusters:6
PolNum: 311740, clusters:6
PolNum: 156677, clusters:3
PolNum: 297192, clusters:3
PolNum: 381353, clusters:4
PolNum: 387456, clusters:4
PolNum: 159592, clusters:5
PolNum: 171612, clusters:1
PolNum: 308748, clusters:5
PolNum: 185669, clusters:1
PolNum: 195192, clusters:3
PolNum: 144277, clusters:0
PolNum: 251475, clusters:6
PolNum: 365495, clusters:6
PolNum: 194036, clusters:1
PolNum: 

PolNum: 391596, clusters:4
PolNum: 127728, clusters:2
PolNum: 23540, clusters:4
PolNum: 501064, clusters:5
PolNum: 297784, clusters:5
PolNum: 307498, clusters:5
PolNum: 385026, clusters:2
PolNum: 337624, clusters:0
PolNum: 19738, clusters:5
PolNum: 334580, clusters:2
PolNum: 297947, clusters:5
PolNum: 505661, clusters:0
PolNum: 368, clusters:0
PolNum: 417797, clusters:7
PolNum: 308643, clusters:1
PolNum: 458872, clusters:6
PolNum: 232587, clusters:2
PolNum: 432509, clusters:3
PolNum: 494282, clusters:6
PolNum: 152360, clusters:0
PolNum: 351438, clusters:5
PolNum: 239656, clusters:4
PolNum: 61540, clusters:2
PolNum: 53200, clusters:2
PolNum: 91433, clusters:7
PolNum: 509475, clusters:5
PolNum: 76016, clusters:1
PolNum: 218778, clusters:7
PolNum: 239329, clusters:2
PolNum: 96537, clusters:5
PolNum: 514950, clusters:6
PolNum: 309980, clusters:0
PolNum: 435765, clusters:7
PolNum: 418468, clusters:2
PolNum: 42393, clusters:0
PolNum: 286791, clusters:4
PolNum: 72282, clusters:4
PolNum: 49779

PolNum: 277039, clusters:6
PolNum: 181233, clusters:2
PolNum: 124135, clusters:6
PolNum: 456947, clusters:0
PolNum: 204814, clusters:4
PolNum: 3873, clusters:2
PolNum: 162010, clusters:1
PolNum: 367714, clusters:4
PolNum: 498727, clusters:5
PolNum: 110223, clusters:6
PolNum: 475676, clusters:1
PolNum: 234419, clusters:1
PolNum: 133930, clusters:0
PolNum: 366160, clusters:6
PolNum: 207536, clusters:1
PolNum: 105251, clusters:1
PolNum: 279021, clusters:2
PolNum: 202791, clusters:0
PolNum: 234561, clusters:4
PolNum: 238734, clusters:7
PolNum: 448705, clusters:6
PolNum: 481122, clusters:2
PolNum: 425709, clusters:6
PolNum: 476760, clusters:0
PolNum: 10498, clusters:6
PolNum: 114957, clusters:4
PolNum: 41288, clusters:1
PolNum: 502115, clusters:5
PolNum: 387070, clusters:5
PolNum: 136364, clusters:5
PolNum: 454513, clusters:4
PolNum: 10148, clusters:2
PolNum: 93499, clusters:0
PolNum: 383126, clusters:4
PolNum: 470087, clusters:1
PolNum: 391679, clusters:5
PolNum: 365355, clusters:0
PolNum:

...

PolNum: 124398, clusters:6
PolNum: 425776, clusters:7
PolNum: 11325, clusters:5
PolNum: 198381, clusters:5
PolNum: 117785, clusters:1
PolNum: 158171, clusters:0
PolNum: 343837, clusters:2
PolNum: 198068, clusters:5
PolNum: 456215, clusters:1
PolNum: 126845, clusters:2
PolNum: 118982, clusters:5
PolNum: 341840, clusters:5
PolNum: 395489, clusters:5
PolNum: 144018, clusters:7
PolNum: 492917, clusters:4
PolNum: 508417, clusters:0
PolNum: 486525, clusters:2
PolNum: 76403, clusters:6
PolNum: 143528, clusters:2
PolNum: 232254, clusters:2
PolNum: 237112, clusters:7
PolNum: 454926, clusters:1
PolNum: 31884, clusters:0
PolNum: 15679, clusters:6
PolNum: 188983, clusters:6
PolNum: 442508, clusters:2
PolNum: 424390, clusters:7
PolNum: 201243, clusters:5
PolNum: 383719, clusters:6
PolNum: 108619, clusters:4
PolNum: 220743, clusters:3
PolNum: 275653, clusters:1
PolNum: 42262, clusters:5
PolNum: 232575, clusters:2
PolNum: 465355, clusters:5
PolNum: 217564, clusters:2
PolNum: 373127, clusters:1
PolNum

PolNum: 342601, clusters:7
PolNum: 233747, clusters:2
PolNum: 168624, clusters:5
PolNum: 258254, clusters:7
PolNum: 68628, clusters:6
PolNum: 497445, clusters:4
PolNum: 310463, clusters:5
PolNum: 428559, clusters:5
PolNum: 12273, clusters:2
PolNum: 110979, clusters:4
PolNum: 119044, clusters:2
PolNum: 354026, clusters:4
PolNum: 209466, clusters:5
PolNum: 480830, clusters:0
PolNum: 469004, clusters:7
PolNum: 219979, clusters:5
PolNum: 275586, clusters:5
PolNum: 228795, clusters:6
PolNum: 161274, clusters:4
PolNum: 90961, clusters:2
PolNum: 381189, clusters:5
PolNum: 389709, clusters:4
PolNum: 222196, clusters:5
PolNum: 413509, clusters:4
PolNum: 108447, clusters:5
PolNum: 435151, clusters:0
PolNum: 358520, clusters:7
PolNum: 263061, clusters:7
PolNum: 408058, clusters:5
PolNum: 327830, clusters:3
PolNum: 378739, clusters:2
PolNum: 215748, clusters:4
PolNum: 416817, clusters:4
PolNum: 500029, clusters:7
PolNum: 111562, clusters:2
PolNum: 153952, clusters:4
PolNum: 285178, clusters:6
PolN

PolNum: 274510, clusters:5
PolNum: 185771, clusters:5
PolNum: 64151, clusters:5
PolNum: 102397, clusters:5
PolNum: 107322, clusters:5
PolNum: 347560, clusters:2
PolNum: 332517, clusters:1
PolNum: 177270, clusters:2
PolNum: 254558, clusters:1
PolNum: 15712, clusters:5
PolNum: 235405, clusters:2
PolNum: 25816, clusters:4
PolNum: 389802, clusters:0
PolNum: 83900, clusters:4
PolNum: 512355, clusters:2
PolNum: 142916, clusters:0
PolNum: 174363, clusters:2
PolNum: 477966, clusters:1
PolNum: 17013, clusters:4
PolNum: 329169, clusters:6
PolNum: 401849, clusters:1
PolNum: 252493, clusters:4
PolNum: 228870, clusters:2
PolNum: 199519, clusters:6
PolNum: 126592, clusters:4
PolNum: 271574, clusters:4
PolNum: 194531, clusters:4
PolNum: 37732, clusters:3
PolNum: 287447, clusters:5
PolNum: 142704, clusters:7
PolNum: 321049, clusters:0
PolNum: 473894, clusters:0
PolNum: 263904, clusters:5
PolNum: 28767, clusters:7
PolNum: 156552, clusters:2
PolNum: 176251, clusters:6
PolNum: 357120, clusters:4
PolNum: 

PolNum: 385189, clusters:2
PolNum: 59391, clusters:6
PolNum: 192479, clusters:5
PolNum: 116130, clusters:2
PolNum: 406355, clusters:7
PolNum: 401468, clusters:1
PolNum: 82557, clusters:1
PolNum: 381336, clusters:1
PolNum: 35, clusters:1
PolNum: 277747, clusters:6
PolNum: 291851, clusters:1
PolNum: 27750, clusters:0
PolNum: 499830, clusters:7
PolNum: 290151, clusters:2
PolNum: 153034, clusters:6
PolNum: 278700, clusters:5
PolNum: 69882, clusters:0
PolNum: 443586, clusters:7
PolNum: 79822, clusters:6
PolNum: 191846, clusters:5
PolNum: 394083, clusters:7
PolNum: 444826, clusters:2
PolNum: 162307, clusters:5
PolNum: 339494, clusters:2
PolNum: 378052, clusters:5
PolNum: 130711, clusters:5
PolNum: 202066, clusters:1
PolNum: 164690, clusters:2
PolNum: 340035, clusters:6
PolNum: 241115, clusters:4
PolNum: 467111, clusters:4
PolNum: 435255, clusters:5
PolNum: 413708, clusters:0
PolNum: 469602, clusters:1
PolNum: 207441, clusters:5
PolNum: 66376, clusters:3
PolNum: 442547, clusters:6
PolNum: 403

PolNum: 268580, clusters:5
PolNum: 317855, clusters:7
PolNum: 274975, clusters:0
PolNum: 69465, clusters:6
PolNum: 174076, clusters:2
PolNum: 320735, clusters:3
PolNum: 236748, clusters:4
PolNum: 484941, clusters:6
PolNum: 476445, clusters:2
PolNum: 444457, clusters:4
PolNum: 435777, clusters:6
PolNum: 347943, clusters:4
PolNum: 198037, clusters:7
PolNum: 361804, clusters:6
PolNum: 67252, clusters:7
PolNum: 296379, clusters:3
PolNum: 66809, clusters:1
PolNum: 359399, clusters:5
PolNum: 351551, clusters:5
PolNum: 261840, clusters:5
PolNum: 515442, clusters:5
PolNum: 309700, clusters:5
PolNum: 103159, clusters:6
PolNum: 337285, clusters:4
PolNum: 86258, clusters:6
PolNum: 389999, clusters:6
PolNum: 175080, clusters:4
PolNum: 102078, clusters:5
PolNum: 120480, clusters:7
PolNum: 55501, clusters:5
PolNum: 81742, clusters:4
PolNum: 13247, clusters:4
PolNum: 514216, clusters:0
PolNum: 434914, clusters:5
PolNum: 268754, clusters:5
PolNum: 106602, clusters:4
PolNum: 348113, clusters:5
PolNum: 

In [34]:
kproto = KPrototypes(n_clusters=7, init='Cao', verbose=2)
clusters = kproto.fit_predict(Xenc_sc, categorical=range(498, 513))
print('Total cost of the algorithm: ', kproto.cost_)
print('Total number of iterations: ', kproto.n_iter_)
score = silhouette_score(Xenc_sc, kproto.labels_, sample_size=30000)
print('Silhouette score Kprototype: ', score)

Initialization method and algorithm are deterministic. Setting n_init to 1.
Init: initializing centroids
Init: initializing clusters
Starting iterations...
Run: 1, iteration: 1/100, moves: 40457, ncost: 26192093.267937712
Run: 1, iteration: 2/100, moves: 10580, ncost: 26010641.880627993
Run: 1, iteration: 3/100, moves: 4571, ncost: 25978178.632057715
Run: 1, iteration: 4/100, moves: 3226, ncost: 25961704.07050315
Run: 1, iteration: 5/100, moves: 2392, ncost: 25951046.398203727
Run: 1, iteration: 6/100, moves: 1873, ncost: 25943456.62185911
Run: 1, iteration: 7/100, moves: 1675, ncost: 25937332.107673883
Run: 1, iteration: 8/100, moves: 1439, ncost: 25933076.714345515
Run: 1, iteration: 9/100, moves: 1188, ncost: 25930069.016137015
Run: 1, iteration: 10/100, moves: 965, ncost: 25928242.471930742
Run: 1, iteration: 11/100, moves: 869, ncost: 25926696.950168174
Run: 1, iteration: 12/100, moves: 837, ncost: 25925520.159941066
Run: 1, iteration: 13/100, moves: 616, ncost: 25924794.73116594


In [35]:
result = {}
for s, c in zip(PolNum, clusters):
    print("PolNum: {}, clusters:{}".format(s, c))
    result[s] = c
import csv
with open('K-proto_result_7clusters.csv', 'w') as f:  
    w = csv.DictWriter(f, result.keys())
    w.writeheader()
    w.writerow(result)

PolNum: 294692, clusters:4
PolNum: 281394, clusters:0
PolNum: 475776, clusters:2
PolNum: 288738, clusters:4
PolNum: 15320, clusters:3
PolNum: 377167, clusters:2
PolNum: 169497, clusters:6
PolNum: 12245, clusters:0
PolNum: 414626, clusters:0
PolNum: 147008, clusters:2
PolNum: 70840, clusters:3
PolNum: 141388, clusters:2
PolNum: 42495, clusters:2
PolNum: 26674, clusters:4
PolNum: 231534, clusters:0
PolNum: 90883, clusters:2
PolNum: 91678, clusters:2
PolNum: 106979, clusters:2
PolNum: 472951, clusters:0
PolNum: 415082, clusters:2
PolNum: 461943, clusters:5
PolNum: 56106, clusters:6
PolNum: 293174, clusters:4
PolNum: 315646, clusters:2
PolNum: 49751, clusters:0
PolNum: 258001, clusters:6
PolNum: 111566, clusters:2
PolNum: 497199, clusters:2
PolNum: 251999, clusters:1
PolNum: 80496, clusters:4
PolNum: 369228, clusters:5
PolNum: 289246, clusters:5
PolNum: 217750, clusters:0
PolNum: 44872, clusters:0
PolNum: 462073, clusters:6
PolNum: 111004, clusters:5
PolNum: 458273, clusters:2
PolNum: 2107

PolNum: 61073, clusters:0
PolNum: 316622, clusters:0
PolNum: 289755, clusters:5
PolNum: 169348, clusters:0
PolNum: 37587, clusters:2
PolNum: 124722, clusters:2
PolNum: 331736, clusters:0
PolNum: 121465, clusters:2
PolNum: 467272, clusters:0
PolNum: 157688, clusters:2
PolNum: 392735, clusters:5
PolNum: 283119, clusters:2
PolNum: 149592, clusters:6
PolNum: 180965, clusters:0
PolNum: 244996, clusters:6
PolNum: 213516, clusters:6
PolNum: 389568, clusters:3
PolNum: 290991, clusters:5
PolNum: 180898, clusters:2
PolNum: 28951, clusters:2
PolNum: 512260, clusters:3
PolNum: 481242, clusters:2
PolNum: 160442, clusters:0
PolNum: 356999, clusters:5
PolNum: 121767, clusters:6
PolNum: 197868, clusters:1
PolNum: 124929, clusters:5
PolNum: 205504, clusters:2
PolNum: 475165, clusters:2
PolNum: 428514, clusters:6
PolNum: 239522, clusters:3
PolNum: 291508, clusters:5
PolNum: 326904, clusters:0
PolNum: 287081, clusters:4
PolNum: 56804, clusters:2
PolNum: 316044, clusters:4
PolNum: 461856, clusters:0
PolNu

PolNum: 486024, clusters:0
PolNum: 82349, clusters:4
PolNum: 437497, clusters:4
PolNum: 486215, clusters:5
PolNum: 150159, clusters:3
PolNum: 469387, clusters:2
PolNum: 327419, clusters:0
PolNum: 300379, clusters:2
PolNum: 483971, clusters:2
PolNum: 103522, clusters:4
PolNum: 92108, clusters:4
PolNum: 428858, clusters:4
PolNum: 203672, clusters:0
PolNum: 18211, clusters:2
PolNum: 162769, clusters:3
PolNum: 201803, clusters:2
PolNum: 503261, clusters:6
PolNum: 112157, clusters:6
PolNum: 410584, clusters:0
PolNum: 149441, clusters:2
PolNum: 392084, clusters:2
PolNum: 421048, clusters:2
PolNum: 418920, clusters:0
PolNum: 311070, clusters:6
PolNum: 483969, clusters:2
PolNum: 367609, clusters:4
PolNum: 67651, clusters:4
PolNum: 397656, clusters:5
PolNum: 418798, clusters:5
PolNum: 116705, clusters:0
PolNum: 48006, clusters:1
PolNum: 460790, clusters:2
PolNum: 108025, clusters:6
PolNum: 400570, clusters:4
PolNum: 150406, clusters:3
PolNum: 324126, clusters:6
PolNum: 267374, clusters:4
PolNum

PolNum: 193071, clusters:5
PolNum: 505522, clusters:6
PolNum: 408347, clusters:0
PolNum: 161483, clusters:2
PolNum: 400538, clusters:0
PolNum: 404071, clusters:0
PolNum: 509202, clusters:4
PolNum: 11318, clusters:0
PolNum: 479551, clusters:5
PolNum: 73414, clusters:5
PolNum: 472491, clusters:5
PolNum: 32598, clusters:2
PolNum: 285873, clusters:5
PolNum: 22742, clusters:2
PolNum: 279398, clusters:0
PolNum: 452133, clusters:0
PolNum: 451097, clusters:6
PolNum: 98083, clusters:3
PolNum: 340699, clusters:6
PolNum: 46800, clusters:0
PolNum: 178865, clusters:6
PolNum: 258045, clusters:2
PolNum: 197502, clusters:0
PolNum: 101266, clusters:6
PolNum: 274492, clusters:2
PolNum: 32868, clusters:2
PolNum: 459081, clusters:0
PolNum: 132818, clusters:0
PolNum: 30232, clusters:2
PolNum: 411053, clusters:2
PolNum: 460791, clusters:2
PolNum: 464533, clusters:4
PolNum: 1935, clusters:2
PolNum: 426331, clusters:0
PolNum: 180799, clusters:1
PolNum: 197187, clusters:2
PolNum: 382042, clusters:5
PolNum: 408

PolNum: 128307, clusters:2
PolNum: 430635, clusters:4
PolNum: 461108, clusters:2
PolNum: 262461, clusters:2
PolNum: 85570, clusters:2
PolNum: 398238, clusters:3
PolNum: 47221, clusters:5
PolNum: 340902, clusters:6
PolNum: 421929, clusters:0
PolNum: 344939, clusters:2
PolNum: 85184, clusters:5
PolNum: 186167, clusters:5
PolNum: 487118, clusters:2
PolNum: 420867, clusters:0
PolNum: 421704, clusters:4
PolNum: 192573, clusters:0
PolNum: 119540, clusters:3
PolNum: 24414, clusters:0
PolNum: 424441, clusters:3
PolNum: 258872, clusters:0
PolNum: 365950, clusters:5
PolNum: 118100, clusters:2
PolNum: 187944, clusters:4
PolNum: 459333, clusters:2
PolNum: 136344, clusters:0
PolNum: 78489, clusters:0
PolNum: 274035, clusters:4
PolNum: 196191, clusters:0
PolNum: 282342, clusters:4
PolNum: 297609, clusters:2
PolNum: 66938, clusters:5
PolNum: 218653, clusters:5
PolNum: 361224, clusters:2
PolNum: 391200, clusters:3
PolNum: 288327, clusters:2
PolNum: 10608, clusters:2
PolNum: 517140, clusters:5
PolNum: 

...

PolNum: 412723, clusters:5
PolNum: 302146, clusters:0
PolNum: 378635, clusters:2
PolNum: 462591, clusters:3
PolNum: 54950, clusters:2
PolNum: 348624, clusters:5
PolNum: 215862, clusters:6
PolNum: 447557, clusters:0
PolNum: 317286, clusters:4
PolNum: 35475, clusters:1
PolNum: 288252, clusters:0
PolNum: 509451, clusters:6
PolNum: 260074, clusters:3
PolNum: 506731, clusters:0
PolNum: 375116, clusters:6
PolNum: 383517, clusters:2
PolNum: 366236, clusters:3
PolNum: 105061, clusters:0
PolNum: 400160, clusters:3
PolNum: 30821, clusters:5
PolNum: 196141, clusters:3
PolNum: 66057, clusters:6
PolNum: 508452, clusters:6
PolNum: 203032, clusters:3
PolNum: 509240, clusters:6
PolNum: 23641, clusters:2
PolNum: 20408, clusters:2
PolNum: 221643, clusters:6
PolNum: 185302, clusters:2
PolNum: 38669, clusters:5
PolNum: 75212, clusters:0
PolNum: 418116, clusters:4
PolNum: 43117, clusters:2
PolNum: 125959, clusters:5
PolNum: 393924, clusters:5
PolNum: 264504, clusters:6
PolNum: 81301, clusters:4
PolNum: 383

PolNum: 323625, clusters:2
PolNum: 409746, clusters:5
PolNum: 203326, clusters:3
PolNum: 469553, clusters:3
PolNum: 154321, clusters:4
PolNum: 258666, clusters:2
PolNum: 162134, clusters:4
PolNum: 78590, clusters:4
PolNum: 297836, clusters:2
PolNum: 285504, clusters:5
PolNum: 233715, clusters:2
PolNum: 373985, clusters:5
PolNum: 124210, clusters:4
PolNum: 345697, clusters:3
PolNum: 247503, clusters:0
PolNum: 164524, clusters:3
PolNum: 512828, clusters:2
PolNum: 286967, clusters:3
PolNum: 226753, clusters:5
PolNum: 392031, clusters:2
PolNum: 51858, clusters:6
PolNum: 342601, clusters:0
PolNum: 233747, clusters:5
PolNum: 168624, clusters:2
PolNum: 258254, clusters:0
PolNum: 68628, clusters:2
PolNum: 497445, clusters:4
PolNum: 310463, clusters:2
PolNum: 428559, clusters:0
PolNum: 12273, clusters:5
PolNum: 110979, clusters:4
PolNum: 119044, clusters:5
PolNum: 354026, clusters:4
PolNum: 209466, clusters:0
PolNum: 480830, clusters:3
PolNum: 469004, clusters:0
PolNum: 219979, clusters:0
PolNu

PolNum: 465445, clusters:2
PolNum: 166771, clusters:2
PolNum: 402466, clusters:6
PolNum: 139846, clusters:6
PolNum: 135062, clusters:5
PolNum: 254765, clusters:0
PolNum: 180650, clusters:0
PolNum: 165375, clusters:2
PolNum: 93834, clusters:6
PolNum: 510454, clusters:5
PolNum: 435415, clusters:6
PolNum: 23035, clusters:2
PolNum: 424952, clusters:3
PolNum: 351533, clusters:0
PolNum: 349486, clusters:5
PolNum: 349208, clusters:4
PolNum: 466441, clusters:2
PolNum: 480770, clusters:0
PolNum: 235566, clusters:2
PolNum: 66204, clusters:6
PolNum: 245877, clusters:0
PolNum: 25603, clusters:2
PolNum: 61304, clusters:4
PolNum: 450030, clusters:1
PolNum: 356483, clusters:2
PolNum: 414158, clusters:2
PolNum: 419063, clusters:5
PolNum: 62260, clusters:0
PolNum: 17807, clusters:2
PolNum: 104994, clusters:6
PolNum: 67406, clusters:2
PolNum: 411082, clusters:4
PolNum: 357651, clusters:4
PolNum: 248198, clusters:0
PolNum: 267467, clusters:0
PolNum: 407047, clusters:0
PolNum: 420372, clusters:0
PolNum: 3

PolNum: 279883, clusters:3
PolNum: 106099, clusters:2
PolNum: 58483, clusters:4
PolNum: 216630, clusters:2
PolNum: 101460, clusters:5
PolNum: 331453, clusters:0
PolNum: 477121, clusters:2
PolNum: 245628, clusters:5
PolNum: 33570, clusters:6
PolNum: 49166, clusters:2
PolNum: 84104, clusters:2
PolNum: 100213, clusters:0
PolNum: 409631, clusters:4
PolNum: 102447, clusters:5
PolNum: 41119, clusters:2
PolNum: 257883, clusters:2
PolNum: 410428, clusters:5
PolNum: 153953, clusters:0
PolNum: 462962, clusters:3
PolNum: 382254, clusters:2
PolNum: 43935, clusters:3
PolNum: 191863, clusters:2
PolNum: 73706, clusters:0
PolNum: 91689, clusters:2
PolNum: 11912, clusters:4
PolNum: 96785, clusters:0
PolNum: 333678, clusters:0
PolNum: 352081, clusters:4
PolNum: 290027, clusters:5
PolNum: 107655, clusters:4
PolNum: 130883, clusters:2
PolNum: 457903, clusters:6
PolNum: 157263, clusters:5
PolNum: 94287, clusters:4
PolNum: 141101, clusters:4
PolNum: 153604, clusters:0
PolNum: 330079, clusters:2
PolNum: 2139

PolNum: 148235, clusters:0
PolNum: 313937, clusters:4
PolNum: 386134, clusters:6
PolNum: 164400, clusters:3
PolNum: 363170, clusters:5
PolNum: 321319, clusters:5
PolNum: 507497, clusters:2
PolNum: 212761, clusters:4
PolNum: 76373, clusters:6
PolNum: 219528, clusters:5
PolNum: 306500, clusters:4
PolNum: 402695, clusters:3
PolNum: 443967, clusters:2
PolNum: 202697, clusters:2
PolNum: 251714, clusters:5
PolNum: 322920, clusters:2
PolNum: 469846, clusters:4
PolNum: 469745, clusters:5
PolNum: 505601, clusters:0
PolNum: 397920, clusters:0
PolNum: 68787, clusters:0
PolNum: 475008, clusters:2
PolNum: 464696, clusters:0
PolNum: 35584, clusters:5
PolNum: 164509, clusters:0
PolNum: 26, clusters:5
PolNum: 494317, clusters:5
PolNum: 322064, clusters:6
PolNum: 454952, clusters:5
PolNum: 418729, clusters:2
PolNum: 481503, clusters:0
PolNum: 160767, clusters:0
PolNum: 64624, clusters:0
PolNum: 290415, clusters:4
PolNum: 282596, clusters:2
PolNum: 356210, clusters:0
PolNum: 71746, clusters:2
PolNum: 39